In [1]:
import torch
import torch.nn as nn
import torch.optim as optim
import torch.backends.cudnn as cudnn
import torch.nn.functional as F

import os
import shutil
import argparse
import numpy as np


import models
import torchvision
import torchvision.transforms as transforms
from utils import cal_param_size, cal_multi_adds


from bisect import bisect_right
import time
import math

import easydict
from tqdm import tqdm

In [2]:
import torch
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device

device(type='cuda')

In [3]:
# parser = argparse.ArgumentParser(description='PyTorch CIFAR Training')
# parser.add_argument('--data', default='./data/', type=str, help='Dataset directory')
# parser.add_argument('--dataset', default='cifar100', type=str, help='Dataset name')
# parser.add_argument('--arch', default='wrn_16_2_aux', type=str, help='student network architecture')
# parser.add_argument('--tarch', default='wrn_40_2_aux', type=str, help='teacher network architecture')
# parser.add_argument('--tcheckpoint', default='wrn_40_2_aux.pth.tar', type=str, help='pre-trained weights of teacher')
# parser.add_argument('--init-lr', default=0.05, type=float, help='learning rate')
# parser.add_argument('--weight-decay', default=5e-4, type=float, help='weight decay')
# parser.add_argument('--lr-type', default='multistep', type=str, help='learning rate strategy')
# parser.add_argument('--milestones', default=[150,180,210], type=list, help='milestones for lr-multistep')
# parser.add_argument('--sgdr-t', default=300, type=int, dest='sgdr_t',help='SGDR T_0')
# parser.add_argument('--warmup-epoch', default=0, type=int, help='warmup epoch')
# parser.add_argument('--epochs', type=int, default=240, help='number of epochs to train')
# parser.add_argument('--batch-size', type=int, default=64, help='batch size')
# parser.add_argument('--num-workers', type=int, default=8, help='the number of workers')
# parser.add_argument('--gpu-id', type=str, default='0')
# parser.add_argument('--manual_seed', type=int, default=0)
# parser.add_argument('--kd_T', type=float, default=3, help='temperature for KD distillation')
# parser.add_argument('--resume', '-r', action='store_true', help='resume from checkpoint')
# parser.add_argument('--evaluate', '-e', action='store_true', help='evaluate model')
# parser.add_argument('--checkpoint-dir', default='./checkpoint', type=str, help='network architecture')
# parser.add_argument('--few-ratio', type=float, default=0.25, help='few-shot ratio of training samples ')


args = easydict.EasyDict({
     # Model parameters
    "data" : './data/',
    "dataset" : 'cifar100',
    'arch' : 'wrn_16_2_aux',
    'tarch' : 'wrn_40_2_aux',
    'tcheckpoint' : './wrn_40_2_aux.pth.tar',
    'init_lr' : 0.05, # learning rate
    'weight_decay' : 5e-4, #'weight decay'
    'lr_type' : 'multistep', # learning rate strategy
    'milestones' : [150,180,210],
    'sgdr_t' : 300,
    'warmup_epoch' : 0,
    'epochs' : 240,
    'batch_size' : 64,
    'num_workers' : 8,
    'gpu_id' : '0',
    'manual_seed' : 0,
    'kd_T' : 3.0,
    'checkpoint_dir' : './checkpoint',
    'few_ratio' : 0.25
#         'gpu' : device
   })



In [4]:
import os

current_path = os.getcwd()
print(current_path)

/home/dhkim/j_directory/cifar100_model/Hierarchical_Self-supervised


In [5]:
# global hyperparameter set
# args = parser.parse_args()
os.environ["CUDA_VISIBLE_DEVICES"] = args.gpu_id



log_txt = current_path + '_'+\
          'tarch' + '_' +  args.tarch + '_'+\
          'arch' + '_' +  args.arch + '_'+\
          'dataset' + '_' +  args.dataset + '_'+\
          'few_ratio'+ '_' +  str(args.few_ratio) + '_'+\
          'seed'+ str(args.manual_seed) +'.txt'

log_dir = current_path + '_'+\
          'tarch' + '_' +  args.tarch + '_'+\
          'arch'+ '_' + args.arch + '_'+\
          'dataset' + '_' +  args.dataset + '_'+\
          'few_ratio'+ '_' +  str(args.few_ratio) + '_'+\
          'seed'+ str(args.manual_seed)

# print(log_txt)

args.checkpoint_dir = os.path.join(args.checkpoint_dir, log_dir)
if not os.path.isdir(args.checkpoint_dir):
    os.makedirs(args.checkpoint_dir)

# if args.resume is False and args.evaluate is False:
#     with open(log_txt, 'a+') as f:
#         f.write("==========\nArgs:{}\n==========".format(args) + '\n')

np.random.seed(args.manual_seed)
torch.manual_seed(args.manual_seed)
torch.cuda.manual_seed_all(args.manual_seed)
torch.set_printoptions(precision=4)




In [6]:
num_classes = 100
trainset = torchvision.datasets.CIFAR100(root=args.data, train=True, download=True,
                                        transform=transforms.Compose([
                                            transforms.RandomCrop(32, padding=4),
                                            transforms.RandomHorizontalFlip(),
                                            transforms.ToTensor(),
                                            transforms.Normalize([0.5071, 0.4867, 0.4408],
                                                                [0.2675, 0.2565, 0.2761])
                                        ]))
from sklearn.model_selection import StratifiedShuffleSplit
labels = [trainset[i][1] for i in range(len(trainset))]
ss = StratifiedShuffleSplit(n_splits=1, test_size=1-args.few_ratio, random_state=0)
train_indices, valid_indices = list(ss.split(np.array(labels)[:, np.newaxis], labels))[0]
trainset = torch.utils.data.Subset(trainset, train_indices)

testset = torchvision.datasets.CIFAR100(root=args.data, train=False, download=True,
                                        transform=transforms.Compose([
                                            transforms.ToTensor(),
                                            transforms.Normalize([0.5071, 0.4867, 0.4408],
                                                                [0.2675, 0.2565, 0.2761]),
                                        ]))
trainloader = torch.utils.data.DataLoader(trainset, batch_size=args.batch_size, shuffle=True,
                                    pin_memory=(torch.cuda.is_available()))

testloader = torch.utils.data.DataLoader(testset, batch_size=args.batch_size, shuffle=False,
                                    pin_memory=(torch.cuda.is_available()))

Files already downloaded and verified
Files already downloaded and verified


In [16]:
print('==> Building model..')
net = getattr(models, args.tarch)(num_classes=num_classes)
net.eval()
resolution = (1, 3, 32, 32)
print('Teacher Arch: %s, Params: %.2fM, Multi-adds: %.2fG'
        % (args.tarch, cal_param_size(net)/1e6, cal_multi_adds(net, resolution)/1e9))
del(net)
net = getattr(models, args.arch)(num_classes=num_classes)
net.eval()
resolution = (1, 3, 32, 32)
print('Student Arch: %s, Params: %.2fM, Multi-adds: %.2fG'
        % (args.arch, cal_param_size(net)/1e6, cal_multi_adds(net, resolution)/1e9))
del(net)


print('load pre-trained teacher weights from: {}'.format(args.tcheckpoint))     
checkpoint = torch.load(args.tcheckpoint, map_location=torch.device('cpu'))
# print(checkpoint)


model = getattr(models, args.arch)
net = model(num_classes=num_classes).cuda()
net =  torch.nn.DataParallel(net)

tmodel = getattr(models, args.tarch)
tnet = tmodel(num_classes=num_classes).cuda()
tnet.load_state_dict(checkpoint['net'])
tnet.eval()
tnet =  torch.nn.DataParallel(tnet)

_, ss_logits = net(torch.randn(2, 3, 32, 32))
# print(_)
# print(ss_logits)
num_auxiliary_branches = len(ss_logits)
print(num_auxiliary_branches)
cudnn.benchmark = True


==> Building model..
Teacher Arch: wrn_40_2_aux, Params: 8.02M, Multi-adds: 0.77G
Student Arch: wrn_16_2_aux, Params: 2.63M, Multi-adds: 0.24G
load pre-trained teacher weights from: ./wrn_40_2_aux.pth.tar
3


In [17]:
class DistillKL(nn.Module):
    """Distilling the Knowledge in a Neural Network"""
    def __init__(self, T):
        super(DistillKL, self).__init__()
        self.T = T

    def forward(self, y_s, y_t):
        p_s = F.log_softmax(y_s/self.T, dim=1)
        p_t = F.softmax(y_t/self.T, dim=1)
        loss = F.kl_div(p_s, p_t, reduction='batchmean') * (self.T**2)
        return loss

In [18]:
def correct_num(output, target, topk=(1,)):
    """Computes the precision@k for the specified values of k"""
    maxk = max(topk)
    batch_size = target.size(0)

    _, pred = output.topk(maxk, 1, True, True)
    correct = pred.eq(target.view(-1, 1).expand_as(pred))

    res = []
    for k in topk:
        correct_k = correct[:, :k].float().sum()
        res.append(correct_k)
    return res


def adjust_lr(optimizer, epoch, args, step=0, all_iters_per_epoch=0):
    cur_lr = 0.
    if epoch < args.warmup_epoch:
        cur_lr = args.init_lr * float(1 + step + epoch*all_iters_per_epoch)/(args.warmup_epoch *all_iters_per_epoch)
    else:
        epoch = epoch - args.warmup_epoch
        cur_lr = args.init_lr * 0.1 ** bisect_right(args.milestones, epoch)

    for param_group in optimizer.param_groups:
        param_group['lr'] = cur_lr
    return cur_lr

In [10]:
def train(epoch, criterion_list, optimizer):
    train_loss = 0.
    train_loss_cls = 0.
    train_loss_div = 0.

    ss_top1_num = [0] * num_auxiliary_branches
    ss_top5_num = [0] * num_auxiliary_branches
    class_top1_num = [0] * num_auxiliary_branches
    class_top5_num = [0] * num_auxiliary_branches
    top1_num = 0
    top5_num = 0
    total = 0

    if epoch >= args.warmup_epoch:
        lr = adjust_lr(optimizer, epoch, args)

    start_time = time.time()
    criterion_cls = criterion_list[0]
    criterion_div = criterion_list[1]

    net.train()
    for batch_idx, (input, target) in enumerate(trainloader):
        batch_start_time = time.time()
        input = input.float().cuda()
        target = target.cuda()

        size = input.shape[1:]
        input = torch.stack([torch.rot90(input, k, (2, 3)) for k in range(4)], 1).view(-1, *size)
        labels = torch.stack([target*4+i for i in range(4)], 1).view(-1)

        if epoch < args.warmup_epoch:
            lr = adjust_lr(optimizer, epoch, args, batch_idx, len(trainloader))

        optimizer.zero_grad()
        logits, ss_logits = net(input, grad=True)
        with torch.no_grad():
            t_logits, t_ss_logits = tnet(input)

        loss_cls = torch.tensor(0.).cuda()
        loss_div = torch.tensor(0.).cuda()

        loss_cls = loss_cls + criterion_cls(logits[0::4], target)
        for i in range(len(ss_logits)):
            loss_div = loss_div + criterion_div(ss_logits[i], t_ss_logits[i].detach())
        
        loss_div = loss_div + criterion_div(logits, t_logits.detach())
        
            
        loss = loss_cls + loss_div
        loss.backward()
        optimizer.step()


        train_loss += loss.item() / len(trainloader)
        train_loss_cls += loss_cls.item() / len(trainloader)
        train_loss_div += loss_div.item() / len(trainloader)

        for i in range(len(ss_logits)):
            top1, top5 = correct_num(ss_logits[i], labels, topk=(1, 5))
            ss_top1_num[i] += top1
            ss_top5_num[i] += top5
        
        class_logits = [torch.stack(torch.split(ss_logits[i], split_size_or_sections=4, dim=1), dim=1).sum(dim=2) for i in range(len(ss_logits))]
        multi_target = target.view(-1, 1).repeat(1, 4).view(-1)
        for i in range(len(class_logits)):
            top1, top5 = correct_num(class_logits[i], multi_target, topk=(1, 5))
            class_top1_num[i] += top1
            class_top5_num[i] += top5

        logits = logits.view(-1, 4, num_classes)[:, 0, :]
        top1, top5 = correct_num(logits, target, topk=(1, 5))
        top1_num += top1
        top5_num += top5
        total += target.size(0)

        print('Epoch:{}, batch_idx:{}/{}, lr:{:.5f}, Duration:{:.2f}, Top-1 Acc:{:.4f}'.format(
            epoch, batch_idx, len(trainloader), lr, time.time()-batch_start_time, (top1_num/(total)).item()))


    ss_acc1 = [round((ss_top1_num[i]/(total*4)).item(), 4) for i in range(num_auxiliary_branches)]
    ss_acc5 = [round((ss_top5_num[i]/(total*4)).item(), 4) for i in range(num_auxiliary_branches)]
    class_acc1 = [round((class_top1_num[i]/(total*4)).item(), 4) for i in range(num_auxiliary_branches)] + [round((top1_num/(total)).item(), 4)]
    class_acc5 = [round((class_top5_num[i]/(total*4)).item(), 4) for i in range(num_auxiliary_branches)] + [round((top5_num/(total)).item(), 4)]
    
    print('Train epoch:{}\nTrain Top-1 ss_accuracy: {}\nTrain Top-1 class_accuracy: {}\n'.format(epoch, str(ss_acc1), str(class_acc1)))

    with open(log_txt, 'a+') as f:
        f.write('Epoch:{}\t lr:{:.5f}\t duration:{:.3f}'
                '\n train_loss:{:.5f}\t train_loss_cls:{:.5f}\t train_loss_div:{:.5f}'
                '\nTrain Top-1 ss_accuracy: {}\nTrain Top-1 class_accuracy: {}\n'
                .format(epoch, lr, time.time() - start_time,
                        train_loss, train_loss_cls, train_loss_div,
                        str(ss_acc1), str(class_acc1)))


In [11]:
def test(epoch, criterion_cls, net):
    global best_acc
    test_loss_cls = 0.

    ss_top1_num = [0] * (num_auxiliary_branches)
    ss_top5_num = [0] * (num_auxiliary_branches)
    class_top1_num = [0] * num_auxiliary_branches
    class_top5_num = [0] * num_auxiliary_branches
    top1_num = 0
    top5_num = 0
    total = 0
    
    net.eval()
    with torch.no_grad():
        for batch_idx, (inputs, target) in enumerate(testloader):
            batch_start_time = time.time()
            input, target = inputs.cuda(), target.cuda()

            size = input.shape[1:]
            input = torch.stack([torch.rot90(input, k, (2, 3)) for k in range(4)], 1).view(-1, *size)
            labels = torch.stack([target*4+i for i in range(4)], 1).view(-1)
            
            logits, ss_logits = net(input)
            loss_cls = torch.tensor(0.).cuda()
            loss_cls = loss_cls + criterion_cls(logits[0::4], target)

            test_loss_cls += loss_cls.item()/ len(testloader)

            batch_size = logits.size(0) // 4
            for i in range(len(ss_logits)):
                top1, top5 = correct_num(ss_logits[i], labels, topk=(1, 5))
                ss_top1_num[i] += top1
                ss_top5_num[i] += top5
                
            class_logits = [torch.stack(torch.split(ss_logits[i], split_size_or_sections=4, dim=1), dim=1).sum(dim=2) for i in range(len(ss_logits))]
            multi_target = target.view(-1, 1).repeat(1, 4).view(-1)
            for i in range(len(class_logits)):
                top1, top5 = correct_num(class_logits[i], multi_target, topk=(1, 5))
                class_top1_num[i] += top1
                class_top5_num[i] += top5

            logits = logits.view(-1, 4, num_classes)[:, 0, :]
            top1, top5 = correct_num(logits, target, topk=(1, 5))
            top1_num += top1
            top5_num += top5
            total += target.size(0)
            

            print('Epoch:{}, batch_idx:{}/{}, Duration:{:.2f}, Top-1 Acc:{:.4f}'.format(
                epoch, batch_idx, len(testloader), time.time()-batch_start_time, (top1_num/(total)).item()))

        ss_acc1 = [round((ss_top1_num[i]/(total*4)).item(), 4) for i in range(len(ss_logits))]
        ss_acc5 = [round((ss_top5_num[i]/(total*4)).item(), 4) for i in range(len(ss_logits))]
        class_acc1 = [round((class_top1_num[i]/(total*4)).item(), 4) for i in range(num_auxiliary_branches)] + [round((top1_num/(total)).item(), 4)]
        class_acc5 = [round((class_top5_num[i]/(total*4)).item(), 4) for i in range(num_auxiliary_branches)] + [round((top5_num/(total)).item(), 4)]
        with open(log_txt, 'a+') as f:
            f.write('test epoch:{}\t test_loss_cls:{:.5f}\nTop-1 ss_accuracy: {}\nTop-1 class_accuracy: {}\n'
                    .format(epoch, test_loss_cls, str(ss_acc1), str(class_acc1)))
        print('test epoch:{}\nTest Top-1 ss_accuracy: {}\nTest Top-1 class_accuracy: {}\n'.format(epoch, str(ss_acc1), str(class_acc1)))

    return class_acc1[-1]


In [12]:
best_acc = 0.  # best test accuracy
start_epoch = 0  # start from epoch 0 or last checkpoint epoch
criterion_cls = nn.CrossEntropyLoss()
criterion_div = DistillKL(args.kd_T)

print('Evaluate Teacher:')
acc = test(0, criterion_cls, tnet)
print('Teacher Acc:', acc)

trainable_list = nn.ModuleList([])
trainable_list.append(net)
optimizer = optim.SGD(trainable_list.parameters(),
                      lr=0.1, momentum=0.9, weight_decay=args.weight_decay, nesterov=True)

criterion_list = nn.ModuleList([])
criterion_list.append(criterion_cls)  # classification loss
criterion_list.append(criterion_div)  # KL divergence loss, original knowledge distillation
criterion_list.cuda()


for epoch in range(start_epoch, args.epochs):
    train(epoch, criterion_list, optimizer)
    acc = test(epoch, criterion_cls, net)

    state = {
        'net': net.module.state_dict(),
        'acc': acc,
        'epoch': epoch,
        'optimizer': optimizer.state_dict()
    }
    torch.save(state, os.path.join(args.checkpoint_dir, str(model.__name__) + '.pth.tar'))

    is_best = False
    if best_acc < acc:
        best_acc = acc
        is_best = True

    if is_best:
        shutil.copyfile(os.path.join(args.checkpoint_dir, str(model.__name__) + '.pth.tar'),
                        os.path.join(args.checkpoint_dir, str(model.__name__) + '_best.pth.tar'))

print('Evaluate the best model:')
print('load pre-trained weights from: {}'.format(os.path.join(args.checkpoint_dir, str(model.__name__) + '_best.pth.tar')))
args.evaluate = True
checkpoint = torch.load(os.path.join(args.checkpoint_dir, str(model.__name__) + '_best.pth.tar'),
                        map_location=torch.device('cpu'))
net.module.load_state_dict(checkpoint['net'])
start_epoch = checkpoint['epoch']
top1_acc = test(start_epoch, criterion_cls, net)

with open(log_txt, 'a+') as f:
    f.write('best_accuracy: {} \n'.format(best_acc))
print('best_accuracy: {} \n'.format(best_acc))
os.system('cp ' + log_txt + ' ' + args.checkpoint_dir)

Evaluate Teacher:
Epoch:0, batch_idx:0/157, Duration:0.12, Top-1 Acc:0.8125
Epoch:0, batch_idx:1/157, Duration:0.03, Top-1 Acc:0.8125
Epoch:0, batch_idx:2/157, Duration:0.03, Top-1 Acc:0.8073
Epoch:0, batch_idx:3/157, Duration:0.03, Top-1 Acc:0.8047
Epoch:0, batch_idx:4/157, Duration:0.03, Top-1 Acc:0.8063
Epoch:0, batch_idx:5/157, Duration:0.03, Top-1 Acc:0.8099
Epoch:0, batch_idx:6/157, Duration:0.03, Top-1 Acc:0.8013
Epoch:0, batch_idx:7/157, Duration:0.03, Top-1 Acc:0.8105
Epoch:0, batch_idx:8/157, Duration:0.03, Top-1 Acc:0.7951
Epoch:0, batch_idx:9/157, Duration:0.03, Top-1 Acc:0.7969
Epoch:0, batch_idx:10/157, Duration:0.03, Top-1 Acc:0.7926
Epoch:0, batch_idx:11/157, Duration:0.03, Top-1 Acc:0.7956
Epoch:0, batch_idx:12/157, Duration:0.03, Top-1 Acc:0.7981
Epoch:0, batch_idx:13/157, Duration:0.03, Top-1 Acc:0.7946
Epoch:0, batch_idx:14/157, Duration:0.03, Top-1 Acc:0.7917
Epoch:0, batch_idx:15/157, Duration:0.03, Top-1 Acc:0.7920
Epoch:0, batch_idx:16/157, Duration:0.03, Top-1 

Epoch:0, batch_idx:140/157, Duration:0.03, Top-1 Acc:0.8073
Epoch:0, batch_idx:141/157, Duration:0.03, Top-1 Acc:0.8073
Epoch:0, batch_idx:142/157, Duration:0.03, Top-1 Acc:0.8070
Epoch:0, batch_idx:143/157, Duration:0.03, Top-1 Acc:0.8074
Epoch:0, batch_idx:144/157, Duration:0.03, Top-1 Acc:0.8074
Epoch:0, batch_idx:145/157, Duration:0.03, Top-1 Acc:0.8077
Epoch:0, batch_idx:146/157, Duration:0.03, Top-1 Acc:0.8074
Epoch:0, batch_idx:147/157, Duration:0.03, Top-1 Acc:0.8067
Epoch:0, batch_idx:148/157, Duration:0.03, Top-1 Acc:0.8067
Epoch:0, batch_idx:149/157, Duration:0.03, Top-1 Acc:0.8067
Epoch:0, batch_idx:150/157, Duration:0.03, Top-1 Acc:0.8069
Epoch:0, batch_idx:151/157, Duration:0.03, Top-1 Acc:0.8073
Epoch:0, batch_idx:152/157, Duration:0.03, Top-1 Acc:0.8068
Epoch:0, batch_idx:153/157, Duration:0.03, Top-1 Acc:0.8069
Epoch:0, batch_idx:154/157, Duration:0.03, Top-1 Acc:0.8070
Epoch:0, batch_idx:155/157, Duration:0.03, Top-1 Acc:0.8070
Epoch:0, batch_idx:156/157, Duration:0.0

Epoch:0, batch_idx:102/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0404
Epoch:0, batch_idx:103/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0403
Epoch:0, batch_idx:104/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0403
Epoch:0, batch_idx:105/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0399
Epoch:0, batch_idx:106/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0397
Epoch:0, batch_idx:107/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0398
Epoch:0, batch_idx:108/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0397
Epoch:0, batch_idx:109/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0396
Epoch:0, batch_idx:110/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0396
Epoch:0, batch_idx:111/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0395
Epoch:0, batch_idx:112/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0394
Epoch:0, batch_idx:113/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0395
Epoch:0, batch_idx:114/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0395
Epoch:0, batch_idx:115/196, lr:0.05000, Duration:0.07, Top-1 Acc

Epoch:0, batch_idx:31/157, Duration:0.01, Top-1 Acc:0.0645
Epoch:0, batch_idx:32/157, Duration:0.01, Top-1 Acc:0.0672
Epoch:0, batch_idx:33/157, Duration:0.01, Top-1 Acc:0.0680
Epoch:0, batch_idx:34/157, Duration:0.01, Top-1 Acc:0.0683
Epoch:0, batch_idx:35/157, Duration:0.01, Top-1 Acc:0.0673
Epoch:0, batch_idx:36/157, Duration:0.01, Top-1 Acc:0.0659
Epoch:0, batch_idx:37/157, Duration:0.01, Top-1 Acc:0.0658
Epoch:0, batch_idx:38/157, Duration:0.01, Top-1 Acc:0.0657
Epoch:0, batch_idx:39/157, Duration:0.01, Top-1 Acc:0.0660
Epoch:0, batch_idx:40/157, Duration:0.01, Top-1 Acc:0.0663
Epoch:0, batch_idx:41/157, Duration:0.01, Top-1 Acc:0.0670
Epoch:0, batch_idx:42/157, Duration:0.01, Top-1 Acc:0.0680
Epoch:0, batch_idx:43/157, Duration:0.01, Top-1 Acc:0.0682
Epoch:0, batch_idx:44/157, Duration:0.01, Top-1 Acc:0.0681
Epoch:0, batch_idx:45/157, Duration:0.01, Top-1 Acc:0.0676
Epoch:0, batch_idx:46/157, Duration:0.01, Top-1 Acc:0.0672
Epoch:0, batch_idx:47/157, Duration:0.01, Top-1 Acc:0.06

Epoch:1, batch_idx:10/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0540
Epoch:1, batch_idx:11/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0560
Epoch:1, batch_idx:12/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0517
Epoch:1, batch_idx:13/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0536
Epoch:1, batch_idx:14/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0521
Epoch:1, batch_idx:15/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0527
Epoch:1, batch_idx:16/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0551
Epoch:1, batch_idx:17/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0564
Epoch:1, batch_idx:18/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0567
Epoch:1, batch_idx:19/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0594
Epoch:1, batch_idx:20/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0588
Epoch:1, batch_idx:21/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0582
Epoch:1, batch_idx:22/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0625
Epoch:1, batch_idx:23/196, lr:0.05000, Duration:0.07, Top-1 Acc:0.0645
Epoch:

...

Epoch:239, batch_idx:91/196, lr:0.00005, Duration:0.07, Top-1 Acc:0.9901
Epoch:239, batch_idx:92/196, lr:0.00005, Duration:0.07, Top-1 Acc:0.9898
Epoch:239, batch_idx:93/196, lr:0.00005, Duration:0.07, Top-1 Acc:0.9899
Epoch:239, batch_idx:94/196, lr:0.00005, Duration:0.07, Top-1 Acc:0.9898
Epoch:239, batch_idx:95/196, lr:0.00005, Duration:0.07, Top-1 Acc:0.9897
Epoch:239, batch_idx:96/196, lr:0.00005, Duration:0.07, Top-1 Acc:0.9899
Epoch:239, batch_idx:97/196, lr:0.00005, Duration:0.07, Top-1 Acc:0.9900
Epoch:239, batch_idx:98/196, lr:0.00005, Duration:0.07, Top-1 Acc:0.9901
Epoch:239, batch_idx:99/196, lr:0.00005, Duration:0.07, Top-1 Acc:0.9902
Epoch:239, batch_idx:100/196, lr:0.00005, Duration:0.07, Top-1 Acc:0.9903
Epoch:239, batch_idx:101/196, lr:0.00005, Duration:0.07, Top-1 Acc:0.9903
Epoch:239, batch_idx:102/196, lr:0.00005, Duration:0.07, Top-1 Acc:0.9904
Epoch:239, batch_idx:103/196, lr:0.00005, Duration:0.07, Top-1 Acc:0.9904
Epoch:239, batch_idx:104/196, lr:0.00005, Durat

Epoch:239, batch_idx:14/157, Duration:0.01, Top-1 Acc:0.6865
Epoch:239, batch_idx:15/157, Duration:0.01, Top-1 Acc:0.6846
Epoch:239, batch_idx:16/157, Duration:0.01, Top-1 Acc:0.6866
Epoch:239, batch_idx:17/157, Duration:0.01, Top-1 Acc:0.6892
Epoch:239, batch_idx:18/157, Duration:0.01, Top-1 Acc:0.6908
Epoch:239, batch_idx:19/157, Duration:0.01, Top-1 Acc:0.6992
Epoch:239, batch_idx:20/157, Duration:0.01, Top-1 Acc:0.7009
Epoch:239, batch_idx:21/157, Duration:0.01, Top-1 Acc:0.7038
Epoch:239, batch_idx:22/157, Duration:0.01, Top-1 Acc:0.7031
Epoch:239, batch_idx:23/157, Duration:0.01, Top-1 Acc:0.7012
Epoch:239, batch_idx:24/157, Duration:0.01, Top-1 Acc:0.7000
Epoch:239, batch_idx:25/157, Duration:0.01, Top-1 Acc:0.7001
Epoch:239, batch_idx:26/157, Duration:0.01, Top-1 Acc:0.6979
Epoch:239, batch_idx:27/157, Duration:0.01, Top-1 Acc:0.6975
Epoch:239, batch_idx:28/157, Duration:0.01, Top-1 Acc:0.6977
Epoch:239, batch_idx:29/157, Duration:0.01, Top-1 Acc:0.7010
Epoch:239, batch_idx:30/

Evaluate the best model:
load pre-trained weights from: /home/dhkim/j_directory/cifar100_model/Hierarchical_Self-supervised_tarch_wrn_40_2_aux_arch_wrn_16_2_aux_dataset_cifar100_few_ratio_0.25_seed0/wrn_16_2_aux_best.pth.tar
Epoch:211, batch_idx:0/157, Duration:0.01, Top-1 Acc:0.7500
Epoch:211, batch_idx:1/157, Duration:0.01, Top-1 Acc:0.7500
Epoch:211, batch_idx:2/157, Duration:0.01, Top-1 Acc:0.7292
Epoch:211, batch_idx:3/157, Duration:0.01, Top-1 Acc:0.7422
Epoch:211, batch_idx:4/157, Duration:0.01, Top-1 Acc:0.7250
Epoch:211, batch_idx:5/157, Duration:0.01, Top-1 Acc:0.7266
Epoch:211, batch_idx:6/157, Duration:0.01, Top-1 Acc:0.7188
Epoch:211, batch_idx:7/157, Duration:0.01, Top-1 Acc:0.7168
Epoch:211, batch_idx:8/157, Duration:0.01, Top-1 Acc:0.6927
Epoch:211, batch_idx:9/157, Duration:0.01, Top-1 Acc:0.6969
Epoch:211, batch_idx:10/157, Duration:0.01, Top-1 Acc:0.6946
Epoch:211, batch_idx:11/157, Duration:0.01, Top-1 Acc:0.6992
Epoch:211, batch_idx:12/157, Duration:0.01, Top-1 Acc

Epoch:211, batch_idx:141/157, Duration:0.01, Top-1 Acc:0.7053
Epoch:211, batch_idx:142/157, Duration:0.01, Top-1 Acc:0.7048
Epoch:211, batch_idx:143/157, Duration:0.01, Top-1 Acc:0.7054
Epoch:211, batch_idx:144/157, Duration:0.01, Top-1 Acc:0.7053
Epoch:211, batch_idx:145/157, Duration:0.01, Top-1 Acc:0.7055
Epoch:211, batch_idx:146/157, Duration:0.01, Top-1 Acc:0.7057
Epoch:211, batch_idx:147/157, Duration:0.01, Top-1 Acc:0.7054
Epoch:211, batch_idx:148/157, Duration:0.01, Top-1 Acc:0.7062
Epoch:211, batch_idx:149/157, Duration:0.01, Top-1 Acc:0.7064
Epoch:211, batch_idx:150/157, Duration:0.01, Top-1 Acc:0.7069
Epoch:211, batch_idx:151/157, Duration:0.01, Top-1 Acc:0.7072
Epoch:211, batch_idx:152/157, Duration:0.01, Top-1 Acc:0.7070
Epoch:211, batch_idx:153/157, Duration:0.01, Top-1 Acc:0.7070
Epoch:211, batch_idx:154/157, Duration:0.01, Top-1 Acc:0.7068
Epoch:211, batch_idx:155/157, Duration:0.01, Top-1 Acc:0.7070
Epoch:211, batch_idx:156/157, Duration:0.01, Top-1 Acc:0.7070
test epo

0